In [1]:
import os
import sys
import re
import numpy as np
import pickle
from scipy.optimize import fmin
import multiprocessing as mp
import functools

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
# statmech library setup
sys.path.append('../../statmechlib')
from statmechlib.preprocessing import select_nodes, to_param_dict, to_param_list, insert_zero_params, rescale_manybody_params
from statmechlib.preprocessing import Trajectory, scale_configuration, pair_dist_cutoff, find_index
from statmechlib.forcefields import sd2_loss, utot_EAM_per_atom, utot_EAM_per_box, ftot_EAM, udif_print, u_core
from statmechlib.preprocessing import universal_eos
from statmechlib.preprocessing import pair_dist, force_targ, get_stats_EAM_per_atom, get_stats_EAM_per_box

In [4]:
target_raw = '../data/target_raw'
target_proc = '../data/target_processed'
working = '../data/working'

In [5]:
# stats_file = 'stats_marinica' # 'stats_samples'
# target_file = 'target_marinica' # 'target_samples'
params_file = 'marinica_params'
# stats_file = 'stats_manyknots' # 'stats_samples'
# target_file = 'target_manyknots' # 'target_samples'
# stats_file = 'stats_manymd' # 'stats_samples'
# target_file = 'target_manymd' # 'target_samples'
stats_file = 'stats_manyall' # 'stats_samples'
target_file = 'target_manyall' # 'target_samples'
# stats_file = 'stats_everything' # 'stats_samples'
# target_file = 'target_everything' # 'target_samples'
stats_md_file = 'stats_onlymd' # 'stats_samples'
target_md_file = 'target_onlymd' # 'stats_samples'

In [6]:
with open(os.path.join(working, stats_file+'.pickle'), 'rb') as fi:
    stats_all = pickle.load(fi)

with open(os.path.join(working, target_file+'.pickle'), 'rb') as fi:
    targets = pickle.load(fi)
    
with open(os.path.join(working, stats_md_file+'.pickle'), 'rb') as fi:
    stats_md = pickle.load(fi)
    
with open(os.path.join(working, target_md_file+'.pickle'), 'rb') as fi:
    targets_md = pickle.load(fi)

with open(os.path.join(working, params_file + '.pickle'), 'rb') as fi:
    param_list = pickle.load(fi)  

In [7]:
def downselect(stats_inp, pair_knots, edens_knots):
    
    # find idices of knots
    pair_index = find_index(pair_knots, stats_inp['hyperparams']['pair'])
    edens_index = find_index(edens_knots, stats_inp['hyperparams']['edens'])
    
    # create boolean arrays with select indices set to True
    p_ix = np.array([True if i in pair_index else False for i in range(len(stats_inp['hyperparams']['pair']))])
    m_ix = np.array([True if i in edens_index else False for i in range(len(stats_inp['hyperparams']['edens']))])

    stats_out = select_nodes(stats_inp, p_ix, m_ix)
    
    return stats_out

In [8]:
pair_knots = [2.22, 2.46, 2.5648975,  2.629795 ,  2.6946925,  2.8663175,  2.973045 ,
        3.0797725,  3.5164725,  3.846445 ,  4.1764175,  4.700845 ,
        4.8953   ,  5.089755 ,  5.3429525,  5.401695 ,  5.4604375]
edens_knots = [ 2.5, 2.8663175, 3.1,  3.5,  4.5]

In [9]:
stats = downselect(stats_all, pair_knots, edens_knots)
print(stats['hyperparams'])
stats_select_md = downselect(stats_md, pair_knots, edens_knots)
print(stats_select_md['hyperparams'])

{u'pair': [2.2200000000000002, 2.46, 2.5648974999999998, 2.6297950000000001, 2.6946924999999999, 2.8663175000000001, 2.9730449999999999, 3.0797724999999998, 3.5164724999999999, 3.8464450000000001, 4.1764175000000003, 4.7008450000000002, 4.8952999999999998, 5.0897550000000003, 5.3429525, 5.4016950000000001, 5.4604375000000003], u'edens': [2.5, 2.8663175000000001, 3.1000000000000001, 3.5, 4.5]}
{u'pair': [2.2200000000000002, 2.46, 2.5648974999999998, 2.6297950000000001, 2.6946924999999999, 2.8663175000000001, 2.9730449999999999, 3.0797724999999998, 3.5164724999999999, 3.8464450000000001, 4.1764175000000003, 4.7008450000000002, 4.8952999999999998, 5.0897550000000003, 5.3429525, 5.4016950000000001, 5.4604375000000003], u'edens': [2.5, 2.8663175000000001, 3.1000000000000001, 3.5, 4.5]}


In [10]:
targets['md'] = targets_md['md']
stats['md'] = stats_select_md['md']

In [11]:
for key in sorted(targets.keys()):
    for box, xyz, ene in zip(targets[key]['box'], targets[key]['xyz'], stats[key]['energy']):
        n = len(xyz)
        vol = np.linalg.det(box)
        corr = float(n*n)/vol
        ene.append([corr])

In [12]:
stats['bcc_npt_langevin_300K']['energy'][0][:]

[array([  0.00000000e+00,   0.00000000e+00,   0.00000000e+00,
          4.32452672e-04,   2.40108437e-01,   1.49699018e+01,
          3.67830273e+01,   6.58053659e+01,   2.44033647e+02,
          4.40325883e+02,   6.80111008e+02,   1.13544979e+03,
          1.32771865e+03,   1.53444986e+03,   1.82571708e+03,
          1.89696652e+03,   1.96972937e+03]),
 array([  0.00000000e+00,   0.00000000e+00,   0.00000000e+00,
          4.37184093e-15,   3.18476767e-07,   2.82775234e-02,
          9.17736776e-01,   9.14748666e+00,   1.69749763e+03,
          1.79543454e+04,   1.02110145e+05,   7.92918644e+05,
          1.48233268e+06,   2.64426772e+06,   5.29910283e+06,
          6.17592659e+06,   7.17934901e+06]),
 array([  0.00000000e+00,   0.00000000e+00,   0.00000000e+00,
          9.35076567e-08,   2.01440000e-03,   1.80322649e+00,
          1.06606591e+01,   3.39604107e+01,   4.65546847e+02,
          1.51515052e+03,   3.61420678e+03,   1.00729590e+04,
          1.37729635e+04,   1.83956954e+

In [13]:
targets['eos_fcc']['weight'] = 0.0
targets['bain']['weight'] = 0.0
targets['eos']['weight'] = 0.0
targets['eos_bcc']['weight'] = 0.0
#targets['liq_5000K']['weight'] = 0.1

In [14]:
targets.keys()

['bcc_npt_langevin_3700K',
 'md',
 'vac_npt_langevin_2000K',
 'relax',
 'screw_111_npt_langevin_2000K',
 'bcc_npt_langevin_300K',
 'i111_npt_langevin_2000K',
 'eos',
 'fcc_npt_langevin_300K',
 'eos_fcc',
 'i110_npt_langevin_2000K',
 'liq_3700K',
 'liq_5000K',
 'eos_bcc',
 'bain']

In [15]:
[(key, targets[key]['weight']) for key in targets.keys()]

[('bcc_npt_langevin_3700K', 1.0),
 ('md', 1.0),
 ('vac_npt_langevin_2000K', 1.0),
 ('relax', 1.0),
 ('screw_111_npt_langevin_2000K', 1.0),
 ('bcc_npt_langevin_300K', 1.0),
 ('i111_npt_langevin_2000K', 1.0),
 ('eos', 0.0),
 ('fcc_npt_langevin_300K', 1.0),
 ('eos_fcc', 0.0),
 ('i110_npt_langevin_2000K', 1.0),
 ('liq_3700K', 1.0),
 ('liq_5000K', 1.0),
 ('eos_bcc', 0.0),
 ('bain', 0.0)]

In [36]:
start_params = []
# start_params.append([ -4.18353755e+00,  -9.63668936e-03,  0.0, -1.00171035e+02,
#          1.90025394e+01,   2.15938317e+01,  -1.39759833e+01,
#          2.16332289e+01,  -3.29542126e+00,   1.70455674e+00,
#          1.41347064e+00,  -9.02958785e-01,  -8.62309098e-01,
#          1.95964588e+00,  -8.70527088e-01,   3.22342700e-02,
#         -1.53866121e+00,   1.37095441e+00,  -4.32896107e+01,
#          4.64461212e+00,   3.23329113e-01,   5.82061842e-02, -0.1])
# start_params.append([ -4.36548916e+00,  -1.11867827e-02,  -1.94093020e+01,
#         -1.40195282e+02,   4.53864231e+01,   1.49756180e+01,
#         -1.36031385e+01,   2.21581200e+01,  -4.61501041e+00,
#          2.06360250e+00,   1.12795645e+00,  -8.01200744e-01,
#         -8.58426028e-01,   1.95860157e+00,  -8.68817546e-01,
#          2.43936831e-02,  -1.54555297e+00,   1.38005891e+00,
#         -5.22754243e+01,   3.98209114e+00,   3.07369702e-01,
#          5.51658454e-02,   1.58601447e+00])
# start_params.append([ -4.16739003e+00,  -4.97036785e-03,  -4.62426912e+02,
#          2.63469650e+02,   1.00253629e+01,   2.05151925e+01,
#         -1.36702712e+01,   2.29129977e+01,  -1.27210473e+01,
#          2.95533783e+00,   8.18470873e-01,  -7.89494754e-01,
#         -8.74455389e-01,   2.10177842e+00,  -9.22682795e-01,
#         -6.93852493e-02,  -1.52166575e+00,   1.40766925e+00,
#          1.52571934e+02,   3.37536873e-01,   6.89310740e-01,
#          4.87102227e-02,   2.79573955e+00])
# start_params.append([ -4.33954858e+00,  -1.02215197e-02,  0.0, -1.12590032e+02,
#          3.06702045e+01,   1.74951979e+01,  -1.33298120e+01,
#          2.13899957e+01,  -3.70881631e+00,   1.56452640e+00,
#          1.27789071e+00,  -8.54623702e-01,  -8.39818015e-01,
#          1.95990543e+00,  -8.75948596e-01,   1.81927625e-02,
#         -1.54683863e+00,   1.38614460e+00,  -4.28747460e+01,
#          4.18974818e+00,   1.56622590e-01,   5.72961538e-02,
#          3.46319317e+00])

# start_params.append([ -4.41712815e+00,  -7.57807965e-03, 0.0, 2.79276814e+02,
#          1.74479561e+02,  -6.59620942e+01,   3.53977481e+01,
#         -1.40546374e+01,   2.11913467e+01,  -4.95603366e+00,
#          8.26392820e-01,   1.26391280e+00,  -9.48799563e-01,
#         -7.79099318e-01,   2.00268261e+00,  -8.90495881e-01,
#         -8.59210993e-03,  -1.54948191e+00,   1.39577855e+00,
#          2.43904610e+02,   3.47694754e+00,  -3.14999583e-01,
#          6.33069119e-02,   5.60287637e+00])

# start_params.append([-4.48347382e+00,  -7.78079006e-03,   2.92055760e+02,
#          1.84809430e+02,  -6.18705307e+01,   3.27735461e+01,
#         -1.36588262e+01,   2.11547368e+01,  -5.45394162e+00,
#          8.02998352e-01,   1.21949599e+00,  -9.43034331e-01,
#         -7.71285316e-01,   2.00564540e+00,  -8.93039729e-01,
#         -9.92574423e-03,  -1.55106037e+00,   1.39898785e+00,
#          2.54912062e+02,   3.19484582e+00,  -3.49947883e-01,
#          6.32970386e-02,   4.13612869e+00])

# start_params.append([ -4.41712815e+00,  -7.57807965e-03, 0.0, 2.79276814e+02,
#          1.74479561e+02,  -6.59620942e+01,   3.53977481e+01,
#         -1.40546374e+01,   2.11913467e+01,  -4.95603366e+00,
#          8.26392820e-01,   1.26391280e+00,  -9.48799563e-01,
#         -7.79099318e-01,   2.00268261e+00,  -8.90495881e-01,
#         -8.59210993e-03,  -1.54948191e+00,   1.39577855e+00,
#          2.43904610e+02,   3.47694754e+00,  -3.14999583e-01,
#          6.33069119e-02])

# start_params.append([ -3.09187534e+00,   1.19622206e-04,  -5.67875917e+02,
#          3.21802084e+02,  -4.71317094e+02,   3.98296604e+02,
#         -1.13270858e+02,   6.03114401e+00,   1.48067908e+01,
#         -1.57531660e+01,   7.80863462e+00,  -2.99246651e+00,
#          7.33596451e-01,  -9.50794219e-01,   1.94186078e+00,
#         -8.83596676e-01,  -1.33608784e-01,  -1.46694544e+00,
#          1.42447434e+00,   7.53865380e+01,   3.29733034e-01,
#          2.18327852e+00,   6.63152141e-02, 0.0])

# start_params.append([ -2.95016477e+00,   3.78177969e-04,  -5.21095611e+02,
#          3.09845244e+02,  -4.69222440e+02,   3.95186037e+02,
#         -1.11630659e+02,   5.36915127e+00,   1.52984702e+01,
#         -1.54915170e+01,   7.53107481e+00,  -2.98591742e+00,
#          7.55346307e-01,  -1.00678488e+00,   1.96634582e+00,
#         -8.71560927e-01,  -1.41820832e-01,  -1.46508000e+00,
#          1.42936365e+00,   7.23805795e+01,   0.0, 9.18071460e-01,
#          2.04259992e+00,   6.28575567e-02,   7.62804667e-03])

# start_params.append([ -3.27882058e+00,  -9.77681860e-04,  -5.95486537e+02,
#          3.42401535e+02,  -4.15497479e+02,   3.71316746e+02,
#         -1.07274610e+02,  -2.93282898e+00,   1.51298572e+01,
#         -1.37454674e+01,   8.16724633e+00,  -3.16850352e+00,
#          8.74607042e-01,  -1.07878768e+00,   1.97939820e+00,
#         -8.26149646e-01,  -1.62437297e-01,  -1.45694910e+00,
#          1.42153527e+00,   1.29203135e+02,  -9.25284676e+00,
#          2.63967417e+00,   2.06410900e+00,   6.03258240e-02*2])

# start_params.append([ -3.56709315e+00,  -2.97358686e-03,  -4.37632666e+02,
#          3.35095381e+02,  -2.95083648e+02,   2.94263473e+02,
#         -8.57731610e+01,  -1.62036228e+01,   1.30838141e+01,
#         -6.46551376e+00,   8.01826587e+00,  -3.58786095e+00,
#          1.25735987e+00,  -1.21627097e+00,   2.04033545e+00,
#         -8.04702913e-01,  -1.92666480e-01,  -1.44083371e+00,
#          1.41816098e+00,   1.70360405e+02,  -1.89070431e+01,
#          7.47139804e+00,   1.20540194e+00,   1.34588181e-01, 0.0])

start_params.append([ -3.82648588e+00,  -3.15395324e-03,  -7.04235860e+02,
         2.24162391e+02,   6.00323185e+01,  -2.50405997e+01,
         3.08538238e+01,  -1.21719898e+01,   1.66904242e+01,
        -3.84273118e+00,   8.34954792e-01,   1.12083715e+00,
        -7.94620177e-01,  -6.05852952e-01,   2.03652986e+00,
        -1.03495446e+00,  -1.20820798e-01,  -1.55518420e+00,
         1.50033948e+00,   2.09695356e+02,   1.05734976e-02,
         3.52470642e+00,  -2.47034958e-01,   1.52735787e-01, -3.0])

multi_pars = start_params
print(multi_pars)

[[-3.82648588, -0.00315395324, -704.23586, 224.162391, 60.0323185, -25.0405997, 30.8538238, -12.1719898, 16.6904242, -3.84273118, 0.834954792, 1.12083715, -0.794620177, -0.605852952, 2.03652986, -1.03495446, -0.120820798, -1.5551842, 1.50033948, 209.695356, 0.0105734976, 3.52470642, -0.247034958, 0.152735787, -3.0]]


In [37]:
def optimize_EAM_mp(pars, targets, stats, utot_func):
    
    output = fmin(sd2_loss, pars, args=(targets, stats, utot_EAM_per_atom, None, 0.05, 1), maxiter=100000, maxfun=100000, disp=0, full_output=1,ftol=1e-6)

    return tuple([output[1], output[0]])

In [ ]:
params_output = []

pool = mp.Pool()

for ieam in range(1):#5, len(stats_opts[it]['hyperparams'])):

    get_sd = functools.partial(sd2_loss, targets=targets, stats=stats, utot_func=utot_EAM_per_atom, ftot_func=None, dl=0.05, verbose=1)

    get_opt = functools.partial(optimize_EAM_mp, targets=targets, stats=stats, utot_func=utot_EAM_per_atom)

    # initial ordering
    print('Initial params:', multi_pars[-1])
    
    #distances = pool.map(get_sd, multi_pars)
    
    distances = [get_sd(multi_pars[-1])]
    
    optimal_params = zip(distances, multi_pars[-1:])
    best_params = sorted(optimal_params, key=lambda param: param[0], reverse=True)
    m_pars = [p[1] for p in best_params]

    print('Best params:', best_params)
    print('ieam:', ieam)
    #m_pars = multi_pars

    for i in range(50):
        #optimal_params = pool.map(get_opt, m_pars)
        optimal_params = [get_opt(m_pars)]
        best_params = sorted(optimal_params, key=lambda param: param[0], reverse=True)
        m_pars = [p[1] for p in best_params]
        
        print("Iteration {}, best params: {}".format(i, best_params))

    print('Final Best params:', best_params)
    
    params_output.append(best_params)

pool.close()
pool.join()

('Initial params:', [-3.82648588, -0.00315395324, -704.23586, 224.162391, 60.0323185, -25.0405997, 30.8538238, -12.1719898, 16.6904242, -3.84273118, 0.834954792, 1.12083715, -0.794620177, -0.605852952, 2.03652986, -1.03495446, -0.120820798, -1.5551842, 1.50033948, 209.695356, 0.0105734976, 3.52470642, -0.247034958, 0.152735787, -3.0])
loss 0.000127875749461 0.000127875749461 0.0
('Best params:', [(0.00012787574946120382, [-3.82648588, -0.00315395324, -704.23586, 224.162391, 60.0323185, -25.0405997, 30.8538238, -12.1719898, 16.6904242, -3.84273118, 0.834954792, 1.12083715, -0.794620177, -0.605852952, 2.03652986, -1.03495446, -0.120820798, -1.5551842, 1.50033948, 209.695356, 0.0105734976, 3.52470642, -0.247034958, 0.152735787, -3.0])])
('ieam:', 0)
loss 0.000127875749461 0.000127875749461 0.0
loss 0.0019796409082 0.0019796409082 0.0
loss 0.000140749824667 0.000140749824667 0.0
loss 0.00012781981659 0.00012781981659 0.0
loss 0.00012938977743 0.00012938977743 0.0
loss 0.000129110218631 0.0

loss 9.89143714628e-05 9.89143714628e-05 0.0
loss 0.000119317316517 0.000119317316517 0.0
loss 0.000107311180273 0.000107311180273 0.0
loss 9.96551088958e-05 9.96551088958e-05 0.0
loss 0.000115616116786 0.000115616116786 0.0
loss 0.000113775956357 0.000113775956357 0.0
loss 0.000108381876347 0.000108381876347 0.0
loss 0.00012530118706 0.00012530118706 0.0
loss 0.000109142537408 0.000109142537408 0.0
loss 0.000107797997334 0.000107797997334 0.0
loss 9.88603177151e-05 9.88603177151e-05 0.0
loss 9.79433463666e-05 9.79433463666e-05 0.0
loss 9.43544997746e-05 9.43544997746e-05 0.0
loss 8.79945295179e-05 8.79945295179e-05 0.0
loss 0.000113484372269 0.000113484372269 0.0
loss 9.4640828788e-05 9.4640828788e-05 0.0
loss 9.6566365493e-05 9.6566365493e-05 0.0
loss 9.57890938805e-05 9.57890938805e-05 0.0
loss 0.000103632797485 0.000103632797485 0.0
loss 0.000103297369015 0.000103297369015 0.0
loss 0.00010318384996 0.00010318384996 0.0
loss 0.000104900121626 0.000104900121626 0.0
loss 9.55496279569

loss 3.09571374664e-05 3.09571374664e-05 0.0
loss 3.23059024711e-05 3.23059024711e-05 0.0
loss 2.92947558732e-05 2.92947558732e-05 0.0
loss 3.04358325205e-05 3.04358325205e-05 0.0
loss 3.15357842477e-05 3.15357842477e-05 0.0
loss 2.91859986518e-05 2.91859986518e-05 0.0
loss 3.32641081826e-05 3.32641081826e-05 0.0
loss 2.89744826153e-05 2.89744826153e-05 0.0
loss 3.20578656306e-05 3.20578656306e-05 0.0
loss 2.90863317621e-05 2.90863317621e-05 0.0
loss 3.07990078563e-05 3.07990078563e-05 0.0
loss 3.12277932307e-05 3.12277932307e-05 0.0
loss 2.91053580645e-05 2.91053580645e-05 0.0
loss 3.11976463755e-05 3.11976463755e-05 0.0
loss 2.90506065448e-05 2.90506065448e-05 0.0
loss 3.0338781427e-05 3.0338781427e-05 0.0
loss 3.09787296552e-05 3.09787296552e-05 0.0
loss 2.90270107873e-05 2.90270107873e-05 0.0
loss 3.10619156325e-05 3.10619156325e-05 0.0
loss 2.90033504797e-05 2.90033504797e-05 0.0
loss 3.09381956073e-05 3.09381956073e-05 0.0
loss 2.90103664327e-05 2.90103664327e-05 0.0
loss 3.09289

loss 2.73165268715e-05 2.73165268715e-05 0.0
loss 2.72907994054e-05 2.72907994054e-05 0.0
loss 2.73766163232e-05 2.73766163232e-05 0.0
loss 2.71760507013e-05 2.71760507013e-05 0.0
loss 2.67851247836e-05 2.67851247836e-05 0.0
loss 2.63873950336e-05 2.63873950336e-05 0.0
loss 2.67722711459e-05 2.67722711459e-05 0.0
loss 2.74182490888e-05 2.74182490888e-05 0.0
loss 2.70177172081e-05 2.70177172081e-05 0.0
loss 2.67857669469e-05 2.67857669469e-05 0.0
loss 2.67654212046e-05 2.67654212046e-05 0.0
loss 2.67186018654e-05 2.67186018654e-05 0.0
loss 2.69185816187e-05 2.69185816187e-05 0.0
loss 2.66815528566e-05 2.66815528566e-05 0.0
loss 2.71700012929e-05 2.71700012929e-05 0.0
loss 2.66610530468e-05 2.66610530468e-05 0.0
loss 2.65442320636e-05 2.65442320636e-05 0.0
loss 2.64257533803e-05 2.64257533803e-05 0.0
loss 2.69066803741e-05 2.69066803741e-05 0.0
loss 2.6592324033e-05 2.6592324033e-05 0.0
loss 2.66862185201e-05 2.66862185201e-05 0.0
loss 2.66290248036e-05 2.66290248036e-05 0.0
loss 2.63489

loss 2.14965059071e-05 2.14965059071e-05 0.0
loss 2.13589803905e-05 2.13589803905e-05 0.0
loss 2.13646365866e-05 2.13646365866e-05 0.0
loss 2.16086976464e-05 2.16086976464e-05 0.0
loss 2.12814282261e-05 2.12814282261e-05 0.0
loss 2.16206659369e-05 2.16206659369e-05 0.0
loss 2.12753318728e-05 2.12753318728e-05 0.0
loss 2.15354959914e-05 2.15354959914e-05 0.0
loss 2.12839258983e-05 2.12839258983e-05 0.0
loss 2.16417887627e-05 2.16417887627e-05 0.0
loss 2.1261745829e-05 2.1261745829e-05 0.0
loss 2.15337079239e-05 2.15337079239e-05 0.0
loss 2.12708033446e-05 2.12708033446e-05 0.0
loss 2.12561323045e-05 2.12561323045e-05 0.0
loss 2.15113069845e-05 2.15113069845e-05 0.0
loss 2.12552650346e-05 2.12552650346e-05 0.0
loss 2.14811481785e-05 2.14811481785e-05 0.0
loss 2.12507410607e-05 2.12507410607e-05 0.0
loss 2.12591460787e-05 2.12591460787e-05 0.0
loss 2.14988718985e-05 2.14988718985e-05 0.0
loss 2.12388278532e-05 2.12388278532e-05 0.0
loss 2.11688399053e-05 2.11688399053e-05 0.0
loss 2.12606

...

loss 5.01076411814e-06 5.01076411814e-06 0.0
loss 5.01053811144e-06 5.01053811144e-06 0.0
loss 5.01134746196e-06 5.01134746196e-06 0.0
loss 5.0103668026e-06 5.0103668026e-06 0.0
loss 5.01007174853e-06 5.01007174853e-06 0.0
loss 5.0104870783e-06 5.0104870783e-06 0.0
loss 5.01052887249e-06 5.01052887249e-06 0.0
loss 5.01039356451e-06 5.01039356451e-06 0.0
loss 5.00987946076e-06 5.00987946076e-06 0.0
loss 5.01075372362e-06 5.01075372362e-06 0.0
loss 5.00980918669e-06 5.00980918669e-06 0.0
loss 5.00957591859e-06 5.00957591859e-06 0.0
loss 5.00852487974e-06 5.00852487974e-06 0.0
loss 5.00985265418e-06 5.00985265418e-06 0.0
loss 5.0096537399e-06 5.0096537399e-06 0.0
loss 5.01015097424e-06 5.01015097424e-06 0.0
loss 5.00926860492e-06 5.00926860492e-06 0.0
loss 5.0090773657e-06 5.0090773657e-06 0.0
loss 5.00921923644e-06 5.00921923644e-06 0.0
loss 5.00878994235e-06 5.00878994235e-06 0.0
loss 5.00882816144e-06 5.00882816144e-06 0.0
loss 5.00893455114e-06 5.00893455114e-06 0.0
loss 5.00841630337

loss 4.97957574621e-06 4.97957574621e-06 0.0
loss 4.97848503309e-06 4.97848503309e-06 0.0
loss 4.97531973064e-06 4.97531973064e-06 0.0
loss 4.9791223047e-06 4.9791223047e-06 0.0
loss 4.97760746142e-06 4.97760746142e-06 0.0
loss 4.98066143411e-06 4.98066143411e-06 0.0
loss 4.97799571662e-06 4.97799571662e-06 0.0
loss 4.9771028718e-06 4.9771028718e-06 0.0
loss 4.9773385839e-06 4.9773385839e-06 0.0
loss 4.97824176185e-06 4.97824176185e-06 0.0
loss 4.97584905565e-06 4.97584905565e-06 0.0
loss 4.97613522488e-06 4.97613522488e-06 0.0
loss 4.97552060432e-06 4.97552060432e-06 0.0
loss 4.97715060713e-06 4.97715060713e-06 0.0
loss 4.97532130264e-06 4.97532130264e-06 0.0
loss 4.9764902779e-06 4.9764902779e-06 0.0
loss 4.97440542653e-06 4.97440542653e-06 0.0
loss 4.97157474963e-06 4.97157474963e-06 0.0
loss 4.97375650354e-06 4.97375650354e-06 0.0
loss 4.97312909967e-06 4.97312909967e-06 0.0
loss 4.97410077154e-06 4.97410077154e-06 0.0
loss 4.97308988087e-06 4.97308988087e-06 0.0
loss 4.97310646417

loss 4.92942158008e-06 4.92942158008e-06 0.0
loss 4.9344451994e-06 4.9344451994e-06 0.0
loss 4.92649831755e-06 4.92649831755e-06 0.0
loss 4.9294854851e-06 4.9294854851e-06 0.0
loss 4.92581095808e-06 4.92581095808e-06 0.0
loss 4.92946958317e-06 4.92946958317e-06 0.0
loss 4.92852546075e-06 4.92852546075e-06 0.0
loss 4.92873180062e-06 4.92873180062e-06 0.0
loss 4.92628123348e-06 4.92628123348e-06 0.0
loss 4.93757980856e-06 4.93757980856e-06 0.0
loss 4.92967805319e-06 4.92967805319e-06 0.0
loss 4.92441914282e-06 4.92441914282e-06 0.0
loss 4.9266419736e-06 4.9266419736e-06 0.0
loss 4.93585140349e-06 4.93585140349e-06 0.0
loss 4.92880973261e-06 4.92880973261e-06 0.0
loss 4.92393533763e-06 4.92393533763e-06 0.0
loss 4.92622990429e-06 4.92622990429e-06 0.0
loss 4.92631983405e-06 4.92631983405e-06 0.0
loss 4.92687195158e-06 4.92687195158e-06 0.0
loss 4.9250892267e-06 4.9250892267e-06 0.0
loss 4.92406535802e-06 4.92406535802e-06 0.0
loss 4.92404816533e-06 4.92404816533e-06 0.0
loss 4.92185671165

loss 4.90332935881e-06 4.90332935881e-06 0.0
loss 4.90184738712e-06 4.90184738712e-06 0.0
loss 4.91027011819e-06 4.91027011819e-06 0.0
loss 4.90638655178e-06 4.90638655178e-06 0.0
loss 4.90590146414e-06 4.90590146414e-06 0.0
loss 4.90453760373e-06 4.90453760373e-06 0.0
loss 4.90685703092e-06 4.90685703092e-06 0.0
loss 4.9080532423e-06 4.9080532423e-06 0.0
loss 4.90860051368e-06 4.90860051368e-06 0.0
loss 4.90592320318e-06 4.90592320318e-06 0.0
loss 4.90560722861e-06 4.90560722861e-06 0.0
loss 4.90374664865e-06 4.90374664865e-06 0.0
loss 4.90855566241e-06 4.90855566241e-06 0.0
loss 4.90574182186e-06 4.90574182186e-06 0.0
loss 4.90489223581e-06 4.90489223581e-06 0.0
loss 4.90389290301e-06 4.90389290301e-06 0.0
loss 4.90538565749e-06 4.90538565749e-06 0.0
loss 4.9029186183e-06 4.9029186183e-06 0.0
loss 4.90397549312e-06 4.90397549312e-06 0.0
loss 4.90452939591e-06 4.90452939591e-06 0.0
loss 4.90388159211e-06 4.90388159211e-06 0.0
loss 4.90645474267e-06 4.90645474267e-06 0.0
loss 4.9042441

loss 4.89712469848e-06 4.89712469848e-06 0.0
loss 4.89671509037e-06 4.89671509037e-06 0.0
loss 4.89619899559e-06 4.89619899559e-06 0.0
loss 4.89614584256e-06 4.89614584256e-06 0.0
loss 4.89714627188e-06 4.89714627188e-06 0.0
loss 4.89577767122e-06 4.89577767122e-06 0.0
loss 4.89590627301e-06 4.89590627301e-06 0.0
loss 4.8972697543e-06 4.8972697543e-06 0.0
loss 4.89679106697e-06 4.89679106697e-06 0.0
loss 4.8970299532e-06 4.8970299532e-06 0.0
loss 4.89586958576e-06 4.89586958576e-06 0.0
loss 4.89609380818e-06 4.89609380818e-06 0.0
loss 4.89709362945e-06 4.89709362945e-06 0.0
loss 4.89571997447e-06 4.89571997447e-06 0.0
loss 4.89618377136e-06 4.89618377136e-06 0.0
loss 4.89558690983e-06 4.89558690983e-06 0.0
loss 4.89596650483e-06 4.89596650483e-06 0.0
loss 4.89682512189e-06 4.89682512189e-06 0.0
loss 4.89574176323e-06 4.89574176323e-06 0.0
loss 4.89668343323e-06 4.89668343323e-06 0.0
loss 4.89601402235e-06 4.89601402235e-06 0.0
loss 4.89651809352e-06 4.89651809352e-06 0.0
loss 4.8966094

In [ ]:
params_output = [(8.9710060363567114e-07, np.array([ -4.18353755e+00,  -9.63668936e-03,  -1.00171035e+02,
         1.90025394e+01,   2.15938317e+01,  -1.39759833e+01,
         2.16332289e+01,  -3.29542126e+00,   1.70455674e+00,
         1.41347064e+00,  -9.02958785e-01,  -8.62309098e-01,
         1.95964588e+00,  -8.70527088e-01,   3.22342700e-02,
        -1.53866121e+00,   1.37095441e+00,  -4.32896107e+01,
         4.64461212e+00,   3.23329113e-01,   5.82061842e-02]))]

In [73]:
params_output = [(8.829397265807305e-07, np.array([ -4.33954858e+00,  -1.02215197e-02,  -1.12590032e+02,
         3.06702045e+01,   1.74951979e+01,  -1.33298120e+01,
         2.13899957e+01,  -3.70881631e+00,   1.56452640e+00,
         1.27789071e+00,  -8.54623702e-01,  -8.39818015e-01,
         1.95990543e+00,  -8.75948596e-01,   1.81927625e-02,
        -1.54683863e+00,   1.38614460e+00,  -4.28747460e+01,
         4.18974818e+00,   1.56622590e-01,   5.72961538e-02,
         3.46319317e+00]))]

In [114]:
params_output = [(8.7421414571196454e-07, np.array([ -4.31249172e+00,  -9.93971047e-03,  -3.76018390e+01,
        -1.14759006e+02,   1.72557600e+01,   2.66437414e+01,
        -1.50817090e+01,   2.22342349e+01,  -3.62963119e+00,
         1.62230813e+00,   1.18480877e+00,  -8.52354746e-01,
        -8.38460594e-01,   1.98957701e+00,  -8.86622667e-01,
         1.66082225e-03,  -1.54824194e+00,   1.39761513e+00,
        -5.06767503e+01,   4.47029066e+00,   9.10205250e-02,
         5.87302830e-02,   1.82639066e+00]))]

In [39]:
params_output = [(8.8257346852300666e-07, np.array([ -4.36548916e+00,  -1.11867827e-02,  -1.94093020e+01,
        -1.40195282e+02,   4.53864231e+01,   1.49756180e+01,
        -1.36031385e+01,   2.21581200e+01,  -4.61501041e+00,
         2.06360250e+00,   1.12795645e+00,  -8.01200744e-01,
        -8.58426028e-01,   1.95860157e+00,  -8.68817546e-01,
         2.43936831e-02,  -1.54555297e+00,   1.38005891e+00,
        -5.22754243e+01,   3.98209114e+00,   3.07369702e-01,
         5.51658454e-02,   1.58601447e+00]))]

In [40]:
params_output = [(2.8925274000958436e-06, np.array([ -3.09187534e+00,   1.19622206e-04,  -5.67875917e+02,
         3.21802084e+02,  -4.71317094e+02,   3.98296604e+02,
        -1.13270858e+02,   6.03114401e+00,   1.48067908e+01,
        -1.57531660e+01,   7.80863462e+00,  -2.99246651e+00,
         7.33596451e-01,  -9.50794219e-01,   1.94186078e+00,
        -8.83596676e-01,  -1.33608784e-01,  -1.46694544e+00,
         1.42447434e+00,   7.53865380e+01,   3.29733034e-01,
         2.18327852e+00,   6.63152141e-02]))]

In [62]:
# convert lists of optimal parameters to dictionaries
params_optimal = []
for pars in params_output:
    #params_optimal.append(to_param_dict(pars, [2, 15, 4, 0]))
    params_optimal.append(to_param_dict(pars[1], stats['hyperparams']))

In [64]:
# store hyperparameters and output parameters in a single file
try:
    with open(os.path.join(working, 'params_store'+'.pickle'), 'rb') as fi:
        params_store = pickle.load(fi)    
except IOError:
    print('no file')
    params_store = []
    
params_store.extend(params_optimal)

with open(os.path.join(working, "params_store.pickle"), 'wb') as fo:
    pickle.dump(params_store, fo, protocol=2)

no file


In [65]:
with open(os.path.join(working, 'params_store' + '.pickle'), 'rb') as fi:
    retreived_params = pickle.load(fi)  

In [66]:
retreived_params

[{'hyperparams': {u'edens': [2.5, 3.1000000000000001, 3.5, 4.9000000000000004],
   u'pair': [2.5648974999999998,
    2.6297950000000001,
    2.6946924999999999,
    2.8663175000000001,
    2.9730449999999999,
    3.0797724999999998,
    3.5164724999999999,
    3.8464450000000001,
    4.1764175000000003,
    4.7008450000000002,
    4.8952999999999998,
    5.0897550000000003,
    5.3429525,
    5.4016950000000001,
    5.4604375000000003]},
  'params': {'edens': array([-43.2896107 ,   4.64461212,   0.32332911,   0.05820618]),
   'embed': array([-4.18353755, -0.00963669]),
   'lrcorr': array([], dtype=float64),
   'pair': array([ -1.00171035e+02,   1.90025394e+01,   2.15938317e+01,
           -1.39759833e+01,   2.16332289e+01,  -3.29542126e+00,
            1.70455674e+00,   1.41347064e+00,  -9.02958785e-01,
           -8.62309098e-01,   1.95964588e+00,  -8.70527088e-01,
            3.22342700e-02,  -1.53866121e+00,   1.37095441e+00])}}]